This notebook is designed for ray integrations for signals

lets load askbid candlesticks file.

In [20]:
import market_trade.constants
import market_trade.dataloader

candlesticks_filepaths = [filepath for filepath in market_trade.constants.CANDLESTICK_DATASETS_PATH.iterdir()]
candlesticks_filepath = candlesticks_filepaths[0]
duka_interface = market_trade.dataloader.DukaMTInterface(candlesticks_filepath)
duka_interface.bid_candlesticks

open     high      low    close    vol                      date
0       0.67323  0.67351  0.67323  0.67351  21.50 2020-09-01 03:00:00+03:00
1       0.67349  0.67350  0.67349  0.67350   5.69 2020-09-01 03:00:05+03:00
2       0.67350  0.67350  0.67350  0.67350   0.00 2020-09-01 03:00:10+03:00
3       0.67355  0.67355  0.67351  0.67351   4.50 2020-09-01 03:00:15+03:00
4       0.67351  0.67352  0.67351  0.67352   7.00 2020-09-01 03:00:20+03:00
...         ...      ...      ...      ...    ...                       ...
380145  0.66212  0.66212  0.66209  0.66209   2.25 2020-10-01 02:58:45+03:00
380146  0.66209  0.66209  0.66209  0.66209   0.00 2020-10-01 02:58:50+03:00
380147  0.66209  0.66209  0.66209  0.66209   0.00 2020-10-01 02:58:55+03:00
380148  0.66209  0.66209  0.66209  0.66209   0.00 2020-10-01 02:59:00+03:00
380149  0.66208  0.66208  0.66207  0.66207   4.00 2020-10-01 02:59:05+03:00

[380150 rows x 6 columns]

Let's test signal.

In [21]:
import market_trade.signals.Signal1

bid_candlesticks_df = duka_interface.bid_candlesticks[:10000]

ind_params = {'MeanType': 'SMA', 'window': 5, 'valueType': 'low', 'kDev': 2}
indEl1 = {
    'df': bid_candlesticks_df,
    'params': ind_params,
    'needFig': False,
    'showOnlyIndex': False,
    'drawFig': True
}
signal_result = market_trade.signals.Signal1.SignalBollingerBands1({'BB': indEl1})
signal_result.analiz

{'chstota': -0.0021010505252626313,
 'zeroNum %': 0.8750375187593797,
 't %': 0.06143071535767884,
 'f %': 0.06353176588294147,
 'toch': 0.49159327461969576}

Now let's design ray trainable.

In [22]:
def trainable(config):
    ind_params = {'MeanType': 'SMA',
                  'window': config['window'],
                  'valueType': config['value_type'],
                  'kDev': config['k_dev']}
    indEl1 = {
        'df': bid_candlesticks_df,
        'params': ind_params,
        'needFig': False,
        'showOnlyIndex': False,
        'drawFig': True
    }
    signal_result = market_trade.signals.Signal1.SignalBollingerBands1({'BB': indEl1})
    tune.report(accuracy=signal_result.analiz["toch"])

Let's create config space.

In [23]:
from ray import tune

config = {
    'window': tune.qrandint(5,100,5),
    'value_type': tune.choice(['open', 'low', 'high', 'close']),
    'k_dev': tune.uniform(1,4)
}

Let's run ray tune

In [24]:
analysis = tune.run(trainable, config=config, num_samples=100, mode='max', metric='accuracy')

2022-06-01 19:33:51,021	WARNING tune.py:636 -- Tune detects GPUs, but no trials are using GPUs. To enable trials to use GPUs, set tune.run(resources_per_trial={'gpu': 1}...) which allows Tune to expose 1 GPU to each trial. You can also override `Trainable.default_resource_request` if using the Trainable API.
2022-06-01 19:33:51,187	INFO trial_runner.py:803 -- starting trainable_9e7a8_00000
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



2022-06-01 19:33:53,205	INFO trial_runner.py:803 -- starting trainable_9e7a8_00001
2022-06-01 19:33:53,215	INFO trial_runner.py:803 -- starting trainable_9e7a8_00002
2022-06-01 19:33:53,228	INFO trial_runner.py:803 -- starting trainable_9e7a8_00003
2022-06-01 19:33:53,244	INFO trial_runner.py:803 -- starting trainable_9e7a8_00004
2022-06-01 19:33:53,262	INFO trial_runner.py:803 -- starting trainable_9e7a8_00005
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

2022-06-01 19:33:53,326	INFO trial_runner.py:803 -- starting trainable_9e7a8_00006
2022-06-01 19:33:53,354	INFO trial_runner.py:803 -- starting trainable_9e7a8_00007
2022-06-01 19:33:53,386	INFO trial_runner.py:803 -- starting trainable_9e7a8_00008
2022-06-

Result for trainable_9e7a8_00000:
  accuracy: 0.46153846153846156
  date: 2022-06-01_19-34-06
  done: false
  experiment_id: dd508a19143b4ab0b6b5466494a701e5
  hostname: parf
  iterations_since_restore: 1
  node_ip: 192.168.1.14
  pid: 9985
  time_since_restore: 13.739934206008911
  time_this_iter_s: 13.739934206008911
  time_total_s: 13.739934206008911
  timestamp: 1654101246
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 9e7a8_00000
  warmup_time: 0.0024194717407226562
  
Result for trainable_9e7a8_00000:
  accuracy: 0.46153846153846156
  date: 2022-06-01_19-34-06
  done: true
  experiment_id: dd508a19143b4ab0b6b5466494a701e5
  experiment_tag: 0_k_dev=3.5873,value_type=close,window=30
  hostname: parf
  iterations_since_restore: 1
  node_ip: 192.168.1.14
  pid: 9985
  time_since_restore: 13.739934206008911
  time_this_iter_s: 13.739934206008911
  time_total_s: 13.739934206008911
  timestamp: 1654101246
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id:

2022-06-01 19:34:08,271	INFO trial_runner.py:803 -- starting trainable_9e7a8_00012


Result for trainable_9e7a8_00003:
  accuracy: 0.49736842105263157
  date: 2022-06-01_19-34-11
  done: false
  experiment_id: 97f33c5e76b746f7a765446ab2136149
  hostname: parf
  iterations_since_restore: 1
  node_ip: 192.168.1.14
  pid: 10023
  time_since_restore: 13.583420276641846
  time_this_iter_s: 13.583420276641846
  time_total_s: 13.583420276641846
  timestamp: 1654101251
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 9e7a8_00003
  warmup_time: 0.005610227584838867
  


...

Result for trainable_9e7a8_00085:
  accuracy: 0.49828178694158076
  date: 2022-06-01_19-36-44
  done: false
  experiment_id: 915dbecc6e4743ed8d6b6ceea4045389
  hostname: parf
  iterations_since_restore: 1
  node_ip: 192.168.1.14
  pid: 14412
  time_since_restore: 14.416006565093994
  time_this_iter_s: 14.416006565093994
  time_total_s: 14.416006565093994
  timestamp: 1654101404
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 9e7a8_00085
  warmup_time: 0.004936695098876953
  
Result for trainable_9e7a8_00088:
  accuracy: 0.5288461538461539
  date: 2022-06-01_19-36-44
  done: false
  experiment_id: 5ccbea3fe82a42128fe3ca5a8c190016
  hostname: parf
  iterations_since_restore: 1
  node_ip: 192.168.1.14
  pid: 14450
  time_since_restore: 14.747365713119507
  time_this_iter_s: 14.747365713119507
  time_total_s: 14.747365713119507
  timestamp: 1654101404
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 9e7a8_00088
  warmup_time: 0.006840944290161133
  
Result 

2022-06-01 19:36:47,794	INFO trial_runner.py:803 -- starting trainable_9e7a8_00097
2022-06-01 19:36:47,803	INFO trial_runner.py:803 -- starting trainable_9e7a8_00098
2022-06-01 19:36:47,835	INFO trial_runner.py:803 -- starting trainable_9e7a8_00099
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Result for trainable_9e7a8_00093:
  accuracy: 0.48841893252769386
  date: 2022-06-01_19-36-50
  done: true
  experiment_id: a055b602ae964ee4b83749c84beb8ceb
  experiment_tag: 93_k_dev=2.2048,value_type=close,window=90
  hostname: parf
  iterations_since_restore: 1
  node_ip: 192.168.1.14
  pid: 14747
  time_since_restore: 11.524987936019897
  time_this_iter_s: 11.524987936019897
  time_total_s: 11.524987936019897
  timestamp: 1654101410
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 9e7a8_00093
  warmup_time: 0.004125833511352539
  
Result for trainable_9e7a8_00095:
  accuracy: 0.5932203389830508
  date: 2022-06-01_19-36-52
  done: false
  experiment_id: 07e454d618834c0f8b1dc16cd1beeb67
  hostname: parf
  iterations_since_restore: 1
  node_ip: 192.168.1.14
  pid: 14861
  time_since_restore: 7.350056171417236
  time_this_iter_s: 7.350056171417236
  time_total_s: 7.350056171417236
  timestamp: 1654101412
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 9

Result for trainable_9e7a8_00099:
  accuracy: 0.5036101083032491
  date: 2022-06-01_19-36-57
  done: true
  experiment_id: 62a7f0d4290c4867b7787f9caa632211
  experiment_tag: 99_k_dev=2.5238,value_type=close,window=80
  hostname: parf
  iterations_since_restore: 1
  node_ip: 192.168.1.14
  pid: 15053
  time_since_restore: 6.573130369186401
  time_this_iter_s: 6.573130369186401
  time_total_s: 6.573130369186401
  timestamp: 1654101417
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 9e7a8_00099
  warmup_time: 0.005975246429443359
  
Result for trainable_9e7a8_00098:
  accuracy: 0.47390396659707723
  date: 2022-06-01_19-36-58
  done: false
  experiment_id: cd2c37116e144082a6da65f8c7d8bfd9
  hostname: parf
  iterations_since_restore: 1
  node_ip: 192.168.1.14
  pid: 15042
  time_since_restore: 6.615413188934326
  time_this_iter_s: 6.615413188934326
  time_total_s: 6.615413188934326
  timestamp: 1654101418
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 9e7a

2022-06-01 19:36:58,602	INFO tune.py:701 -- Total run time: 187.59 seconds (187.44 seconds for the tuning loop).


Let's see who was the best

In [31]:
analysis.best_config

{'window': 100, 'value_type': 'low', 'k_dev': 3.9285854094927943}